In [1]:
import os
import re
import pandas as pd
import urllib
from nltk import SnowballStemmer
from gensim.models import Word2Vec
#import langdetect
import tika
import time
from tika import parser
import pickle

# Raw Articles pdf Data
Convert pdf to text using Tika apache server 

In [2]:
# specify the target data folder
target_dir = 'C:/Thesis/Data/International_Journal_of_Human_Resource_Management'

In [3]:
# prep pdf extraction
pdf_files = []
wrd_files = []

for f in os.listdir(target_dir):
    if f.endswith(".pdf") | f.endswith(".PDF"):
        thispdf = os.path.join(target_dir, f)
        pdf_files = pdf_files + [thispdf]
    if f.endswith(".doc") | f.endswith(".docx") | f.endswith(".DOC") | f.endswith(".DOCX"):
        thiswrd = os.path.join(target_dir, f)
        wrd_files = wrd_files + [thiswrd]

In [4]:
port = 4321 # port to use for Tika server (chosen arbitrarily)
server_str = 'http://localhost:' + str(port)
tika_path  = 'C:\Software\ tika-server-1.23.jar'
tika_run   = 'java -jar' + tika_path + ' --port ' + str(port)
print('Command to start Tika:')
print(tika_run)
print('---')
print('Number of pdf files: ' + str(len(pdf_files)))
print('Number of word files: ' + str(len(wrd_files)))

Command to start Tika:
java -jarC:\Software\ tika-server-1.23.jar --port 4321
---
Number of pdf files: 1632
Number of word files: 0


# pdf metadata

In [5]:
# process the PDF files, store text in memory
tika.TikaClientOnly = True 

pdf_metadata = [parser.from_file(t, server_str, xmlContent=False)["metadata"] for t in (pdf_files + wrd_files)]

In [12]:
pdf_metadata

[{'Content-Type': 'application/pdf',
  'Creation-Date': '2010-06-24T09:28:30Z',
  'Last-Modified': '2020-02-27T17:52:35Z',
  'Last-Save-Date': '2020-02-27T17:52:35Z',
  'X-Parsed-By': ['org.apache.tika.parser.DefaultParser',
   'org.apache.tika.parser.pdf.PDFParser'],
  'X-TIKA:EXCEPTION:warn': 'org.xml.sax.SAXParseException; Premature end of file.\r\n\tat org.apache.xerces.parsers.DOMParser.parse(Unknown Source)\r\n\tat org.apache.xerces.jaxp.DocumentBuilderImpl.parse(Unknown Source)\r\n\tat javax.xml.parsers.DocumentBuilder.parse(Unknown Source)\r\n\tat org.apache.tika.utils.XMLReaderUtils.buildDOM(XMLReaderUtils.java:407)\r\n\tat org.apache.tika.parser.pdf.PDMetadataExtractor.loadDOM(PDMetadataExtractor.java:241)\r\n\tat org.apache.tika.parser.pdf.PDMetadataExtractor.extract(PDMetadataExtractor.java:62)\r\n\tat org.apache.tika.parser.pdf.PDFParser.extractMetadata(PDFParser.java:273)\r\n\tat org.apache.tika.parser.pdf.PDFParser.parse(PDFParser.java:155)\r\n\tat org.apache.tika.parser

# pdf content

In [ ]:
# process the PDF files, store text in memory
tika.TikaClientOnly = True 

#pdf_text = [parser.from_file(t, server_str, xmlContent=False)["content"] for t in (pdf_files + wrd_files)]

# Load pdf content

In [8]:
import pickle
#load the text data
pdf_data = pickle.load(open("C:/Thesis/Data/save/International_Journal_of_Human_Resource_Management/save_alltextData.p", "rb"))


In [9]:
pdf_data[10]

'\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\nThe challenge of increasing minority-group professional representation in the United States: intriguing \n\nfindings \n\n \n\nBy: E. Holly Buttner, Kevin B. Lowe, and Lenora Billings-Harris  \n\n \n\nButtner, E. Holly, Kevin B. Lowe, and Lenora Billings-Harris. ―The challenge of increasing minority-group  \n\nprofessional representation in the United States: intriguing findings.‖ The International Journal of \n\nHuman Resource Management, Vol. 20, No. 4, April 2009, 771–789. DOI: \n\n10.1080/09585190902770604 \n\n \n\nMade available courtesy of Taylor & Francis: \n\nhttp://www.informaworld.com/openurl?genre=journal&issn=0958-5192 \n\n \n\n***Reprinted with permission.. No further reproduction is authorized without written permission from \n\nTaylor & Francis. This version of the document is not the version of record. Figures and/or pictures may \n\nbe missing from this format of the document.*** \n\n \n\nA

# Get title, author and creator from metadata

In [14]:
pdf_title = []
pdf_Author = []
pdf_subject = []
#pdf_creator =[]
#pdf_Keywords = []

for i in pdf_metadata:
    try:
        temp = i['title']
        auth_temp = i['Author']
        t_auth_temp = i['author']
        subj_temp = i['subject']
       #cre_temp = i['creator']
        #key_temp = i['Keywords']
        
        
        pdf_title.append(temp) 
        pdf_Author.append(auth_temp) 
        pdf_subject.append(subj_temp) 
        #pdf_creator.append(cre_temp)
        #pdf_Keywords.append(key_temp)
    except:
        #print("An exception occurred" )
        pdf_title.append(temp)
        pdf_Author.append(auth_temp)
        pdf_subject.append(subj_temp)
        #pdf_creator.append(cre_temp)
        #pdf_Keywords.append(key_temp)

NameError: name 'auth_temp' is not defined

# Get country name

In [4]:
# Since it is case sensetive, firstly get the list of country before converting the text to lowercase
country_list = []
import pycountry

for country in pycountry.countries:
    for i in pdf_text:
        if country.name in i:
            #print(country.name)
            country_list.append(country.name)

In [5]:
#Convert country list to lower case. it will be called in filter function
country_lower = [x.lower() for x in country_list]
#country_lower[1]

# Get Cities name

In [6]:
from geotext import GeoText

cities_list = []
for i in pdf_text:
    place = GeoText(i)
    place.cities
    cities_list.append(place.cities)

In [7]:
#Convert cities list to lower case. it will be called in filter function
cities_lower =[]
for i in cities_list:
    for j in i:
        cities_lower.append(j.lower())
#cities_lower       

# 2 -  Convert pdf text to lower case

In [8]:
#Convert each string to lowercase
for i in range(len(pdf_text)):
    pdf_text[i] = pdf_text[i].lower()

In [9]:
# remove references section 
import re
pdf_ref = [re.sub(r"(?is)\nreferences\n.+", "", f) for f in pdf_text]

In [ ]:
# not required
def eliminate_method_result(method, discussion):
    
    import re    
    start = method
    end = discussion
    #start of pattern, followed by any number of times 'any character OR a newline' and terminated by the end pattern.
    pattern = start + '.*'+'(.|\n)*'+end
    pdf_method_dis = [re.sub(pattern, '', f) for f in pdf_text]

    return pdf_method_dis

In [ ]:
# not required
def eliminate_method_result_ref(method, dis, ref):
    
    import re

    start = method
    end = dis
    
    #start of pattern, followed by any number of times 'any character OR a newline' and terminated by the end pattern.
    pattern = start + '.*'+'(.|\n)*'+end
    pdf_method_dis = [re.sub(pattern, '', f) for f in pdf_text]
    
    start_ref = ref
    pattern_ref = start_ref +'(.|\n)*$'

    pdf_ref= [re.sub(pattern_ref, '', f) for f in pdf_method_dis]
    
    return pdf_ref

# 3 - Pre-processing
Regular expression is used to clean up the pre-processed data and saved as a Master data

In [10]:
import re
pdf_p = [re.sub("r[\S]+\.(net|com|org|info|edu|gov|uk|de|ca|jp|fr|au|us|ru|ch|it|nel|se|no|es|mil)[\S]*\s?", " ", t)for t in pdf_ref]
#remove hyphon only if it is at the end of the line.
pdf_p = [re.sub(r'-\n(\w+ *)', r'\1\n', t) for t in pdf_p]
# remove urls
pdf_p = [re.sub( r'https?://[^\s<>"]+|www\.[^\s<>"]+', "", t)for t in pdf_p]
#remove email address          
pdf_p = [re.sub(r'\w+@\w+\.(?:com|net|org|live|edu)', "", t)for t in pdf_p]
#remove text within ()
pdf_p = [re.sub(r"\([^)]*\)", "", t)for t in pdf_p]
# remove text with [] eg citation
pdf_p = [re.sub(r"\[[^)]*\]", "", t)for t in pdf_p]
#Remove numbers
pdf_p = [re.sub('[0-9]+', '', f) for f in pdf_p]
# remove single characters
pdf_p = [re.sub(' [a-z] ' ,  ' ', f) for f in pdf_p]

pdf_p = [re.sub(' [a-z]\.', '.', f) for f in pdf_p]

pdf_p = [re.sub(' \.', '.', f) for f in pdf_p]

pdf_p = [re.sub('[\n\r]+', ' ', f) for f in pdf_p]
pdf_p = [re.sub('[!@/%#$]', ' ', f) for f in pdf_p]
pdf_p = [re.sub(r"\s\([A-Z][a-z]+,\s[A-Z][a-z]?\.[^\)]*,\s\d{4}\)", "", f) for f in pdf_p]
# save all periods, exclamation marks and question marks, but get rid of unnecessary characters
pdf_p = [re.sub('[\.!?]+ ', 'XYZXYZ', t) for t in pdf_p]
pdf_p = [re.sub('\W*-\W*', ' ', f) for f in pdf_p] # woordreparatie :)
pdf_p = [re.sub('[\W_]+', ' ', f) for f in pdf_p]
pdf_p = [re.sub('XYZXYZ', '. ', f) for f in pdf_p]
#pdf_p[0]

In [11]:
#pdf_p

In [12]:
# Authors names are saved already (code is available at author name folder-get name list notebook)
#load authors names
import pickle
author_name = pickle.load(open("C:/Thesis/Data/save/Master_Data/auth_ref_filter_num_char/auth_International_Journal_of_Human_Resource_Management.p", "rb"))

In [13]:
# GET REFERENCE LISTS OF STOPWORDS, I.E. WORDS THAT ARE ESSENTIALLY MEANINGLESS
# Get all the list of authors names

from nltk.corpus import stopwords

sw = stopwords.words('english') + author_name + country_lower + cities_lower

#print(sw)

In [14]:
# Function to filter out the stopwords and authors names
def filterWords(msg, words):
    m = msg.split(' ')
    words_end = [w + '.' for w in words]
    filtered_words = list(filter(lambda word: word not in words, m))
    filtered_words = [(w if w not in words_end else '.') for w in filtered_words]
    result = ' '.join(filtered_words)
    return(result)

In [15]:
# GET RID OF THE STOPWORDS IN TEXTS
data_proc_1 = [filterWords(f, sw) for f in pdf_p]

In [ ]:
data_proc_1[11]

In [16]:
stopwords = ['a', 'about', 'above', 'across', 'after', 'afterwards']
stopwords += ['again', 'against', 'all', 'almost', 'alone', 'along']
stopwords += ['already', 'also', 'although', 'always', 'am', 'among']
stopwords += ['amongst', 'amoungst', 'amount', 'an', 'and', 'another']
stopwords += ['any', 'anyhow', 'anyone', 'anything', 'anyway', 'anywhere']
stopwords += ['are', 'around', 'as', 'at', 'back', 'be', 'became']
stopwords += ['because', 'become', 'becomes', 'becoming', 'been']
stopwords += ['before', 'beforehand', 'behind', 'being', 'below']
stopwords += ['beside', 'besides', 'between', 'beyond', 'bill', 'both']
stopwords += ['bottom', 'but', 'by', 'call', 'can', 'cannot', 'cant']
stopwords += ['co', 'computer', 'con', 'could', 'couldnt', 'cry', 'de']
stopwords += ['describe', 'detail', 'did', 'do', 'done', 'down', 'due']
stopwords += ['during', 'each', 'eg', 'eight', 'either', 'eleven', 'else']
stopwords += ['elsewhere', 'empty', 'enough', 'etc', 'even', 'ever']
stopwords += ['every', 'everyone', 'everything', 'everywhere', 'except']
stopwords += ['few', 'fifteen', 'fifty', 'fill', 'find', 'fire', 'first']
stopwords += ['five', 'for', 'former', 'formerly', 'forty', 'found']
stopwords += ['four', 'from', 'front', 'full', 'further', 'get', 'give']
stopwords += ['go', 'had', 'has', 'hasnt', 'have', 'he', 'hence', 'her']
stopwords += ['here', 'hereafter', 'hereby', 'herein', 'hereupon', 'hers']
stopwords += ['herself', 'him', 'himself', 'his', 'how', 'however']
stopwords += ['hundred', 'i', 'ie', 'if', 'in', 'inc', 'indeed']
stopwords += ['interest', 'into', 'is', 'it', 'its', 'itself', 'keep']
stopwords += ['last', 'latter', 'latterly', 'least', 'less', 'ltd', 'made']
stopwords += ['many', 'may', 'me', 'meanwhile', 'might', 'mill', 'mine']
stopwords += ['more', 'moreover', 'most', 'mostly', 'move', 'much']
stopwords += ['must', 'my', 'myself', 'name', 'namely', 'neither', 'never']
stopwords += ['nevertheless', 'next', 'nine', 'no', 'nobody', 'none']
stopwords += ['noone', 'nor', 'not', 'nothing', 'now', 'nowhere', 'of']
stopwords += ['off', 'often', 'on','once', 'one', 'only', 'onto', 'or']
stopwords += ['other', 'others', 'otherwise', 'our', 'ours', 'ourselves']
stopwords += ['out', 'over', 'own', 'part', 'per', 'perhaps', 'please']
stopwords += ['put', 'rather', 're', 's', 'same', 'see', 'seem', 'seemed']
stopwords += ['seeming', 'seems', 'serious', 'several', 'she', 'should']
stopwords += ['show', 'side', 'since', 'sincere', 'six', 'sixty', 'so']
stopwords += ['some', 'somehow', 'someone', 'something', 'sometime']
stopwords += ['sometimes', 'somewhere', 'still', 'such', 'system', 'take']
stopwords += ['ten', 'than', 'that', 'the', 'their', 'them', 'themselves']
stopwords += ['then', 'thence', 'there', 'thereafter', 'thereby']
stopwords += ['therefore', 'therein', 'thereupon', 'these', 'they']
stopwords += ['thick', 'thin', 'third', 'this', 'those', 'though', 'three']
stopwords += ['three', 'through', 'throughout', 'thru', 'thus', 'to']
stopwords += ['together', 'too', 'top', 'toward', 'towards', 'twelve']
stopwords += ['twenty', 'two', 'un', 'under', 'until', 'up', 'upon']
stopwords += ['us', 'very', 'via', 'was', 'we', 'well', 'were', 'what']
stopwords += ['whatever', 'when', 'whence', 'whenever', 'where']
stopwords += ['whereafter', 'whereas', 'whereby', 'wherein', 'whereupon']
stopwords += ['wherever', 'whether', 'which', 'while', 'whither', 'who']
stopwords += ['whoever', 'whole', 'whom', 'whose', 'why', 'will', 'with']
stopwords += ['within', 'without', 'would', 'yet', 'you', 'your']
stopwords += ['yours', 'yourself', 'yourselves']

In [17]:
data_proc = [filterWords(f, stopwords) for f in data_proc_1]

In [ ]:
#data_proc[0]

In [18]:
data_proc = [re.sub('\s([?.!"](?:\s|$))' , r'\1', f) for f in data_proc]
data_proc = [re.sub("^\s+","", f) for f in data_proc]
data_proc = [re.sub("\s+\Z","", f) for f in data_proc]

In [19]:
#data_proc

In [20]:
# save data
pickle.dump(data_proc, open( "C:/Thesis/Data/save/Master_Data/MD_2/data_proc_latest/IJHRM_data_proc.p", "wb" ) )

In [21]:
#import io
with open("C:/Thesis/Data/save/Master_Data/MD_2/data_proc_latest/IJHRM_data_proc_txt.txt", "w",encoding="utf-8") as outfile:
    for i in range(len(data_proc)):
        outstring = ""
        outstring += str(data_proc[i])
        outfile.write(outstring)